# Introduction

This notebook will walk you through creating and monitoring your HITs. 

It provides methods to create HITs, pretty-print HIT and assignment status, expire/edit HITs, create qualifications, and download collected data. 

Before continuing, make sure that you have read the README and set all config fields to their desired values.

## Requirements: 

This code requires Python3 and the following packages: 
- boto3 
- beautiful soup 4

Before using, you will have to set up an authentication key to use the Amazon API and include it in a credentials file. See here: https://aws.amazon.com/developers/getting-started/python/

# Setup

Read the config file and establish a connection to MTurk.

A connection is made to production or to the sandbox based on values in the config. 

In [5]:
import datetime
import boto3
import json
import copy
import pprint
from bs4 import BeautifulSoup as bs 
from uuid import uuid4
import csv
import os

In [6]:
# path to the config file 
CONFIG_PATH = "../config.json"

# where to save downloaded results 
SAVE_PATH = "assignments.json" 

# AWS profile to use
AWS_PROFILE_NAME = "memento"

In [7]:
USING_PROD = None
EXTERNAL_SUBMIT = None

# Read config and extract relevant settings
with open(CONFIG_PATH, 'r') as f:
    config = json.loads(f.read())
    
hit_config = config['hitCreation']

EXTERNAL_SUBMIT = config['advanced']['externalSubmit']

# Connection to production or sandbox 
if hit_config['production']:
    print("USING PROD")
    USING_PROD = True
    endpoint_url = 'https://mturk-requester.us-east-1.amazonaws.com'
    origin="production"
else:
    print("USING SANDBOX")
    USING_PROD = False
    endpoint_url = 'https://mturk-requester-sandbox.us-east-1.amazonaws.com'
    origin="sandbox"
    
hit_url = hit_config['taskUrl']
# If using an external link, add a querystring origin=sandbox or origin=production 
# for use in your js logic if you want. Not done for MTurk submits because it breaks the submit link
if (config['advanced']['externalSubmit']): 
    hit_url = "%s?origin=%s" % (hit_url, origin)
    
# Create an API connection
session = boto3.session.Session(profile_name=AWS_PROFILE_NAME)
cl = session.client('mturk', region_name='us-east-1', endpoint_url=endpoint_url)

print("Configuring task as external link with data submitted to: %s" % config['advanced']['externalSubmitUrl'] if EXTERNAL_SUBMIT else "Configuring task as an iframe within Mturk")
print("TASK URL: " + hit_url)


USING PROD
Configuring task as an iframe within Mturk
TASK URL: https://memento-game.csail.mit.edu/


# Make new HIT

In [21]:
# Safety flags that prevent you from accidentally messing up your HITs. 
# Set to False except when you are performing these specific tasks. 
ALLOW_HIT_CREATION = True
ALLOW_ASSIGNMENT_ADDITION = False
ALLOW_CREATE_QUAL = False
ALLOW_UPDATE_EXPIRATION = False

In [22]:
# List of qualifications that you will use to filter potential workers. 
# These require that workers come from the US and have an approval rating >= 95%
# Edit this list to specify different qualifications for workers 
QUALS = [
       {
           'QualificationTypeId': '00000000000000000071',
           'Comparator': 'EqualTo',
           'LocaleValues': [{
               'Country': 'US',
           }],
       },
        
       {
           'QualificationTypeId': '000000000000000000L0',
           'Comparator': 'GreaterThanOrEqualTo',
           'IntegerValues': [
               95
           ],
       },
    ]

In [23]:
# Helpers for creating HITs. 

# generic helper that sets metadata fields based on the config file.
def create_hit(task, questionText, quals=QUALS): 
    response = cl.create_hit(
        MaxAssignments=task['numAssignments'],
        AutoApprovalDelayInSeconds=604800,
        LifetimeInSeconds=task['lifetime'],
        AssignmentDurationInSeconds=task['duration'],
        Reward=task['rewardAmount'],
        Title=task['title'],
        Keywords=task['keywords'],
        Description=task['description'],
        Question=questionText,
        QualificationRequirements=quals,
    )
    print(response)
    print("\n")

# creates a HIT in the form of an External Question inside an iFrame
def create_hit_iframe(task):
    questionText = "<ExternalQuestion xmlns=\"http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/"
    questionText += "2006-07-14/ExternalQuestion.xsd\">\n<ExternalURL>" + task['taskUrl']
    questionText += "</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>"
    create_hit(task, questionText)
    
# Helper to create a HIT in the form of a simple UI with a link to an external page and an
# input box for a completion code 
def create_hit_external(task):
    with open('questionform_template.xml', 'r') as myfile:
        template=myfile.read() 
    question_xml = template % (hit_config["title"], hit_config["description"], task['taskUrl'])
    create_hit(task, question_xml)

In [24]:
# Use this cell to launch your HIT! 
if ALLOW_HIT_CREATION: 
    if not (hit_config.get('variants', False) or hit_config.get('numTasks', False)): 
        raise RuntimeError("You must specify either hitCreation.numTasks or hitCreation.variants in your config.json file")
    
    hit_creation_function = create_hit_external if EXTERNAL_SUBMIT else create_hit_iframe
    
    if hit_config.get('numTasks', False): 
        print("creating " + str(hit_config['numTasks']) + " tasks")
        for i in range(hit_config['numTasks']):
            hit_creation_function(hit_config)
    else: 
        print("creating " + str(len(config['variants'])) + " variants")
        for var in hit_config['variants']: 
            task = copy.deepcopy(config)
            task.update(var)
            hit_creation_function(task)
else: 
    raise RuntimeError("This action is not currently enabled; set `ALLOW_HIT_CREATION` to true to proceed with this action")

creating 100 tasks
{'HIT': {'HITId': '3TZDZ3Y0JULQ0A7UBJEPXZJ5M8X91C', 'HITTypeId': '3YWCO65Q5IJFBBBHQUQRP5I9B3WQ03', 'HITGroupId': '3CL9ACF21N3XOSJBS5A8GX3DPU6W65', 'CreationTime': datetime.datetime(2019, 3, 4, 4, 48, 5, tzinfo=tzlocal()), 'Title': 'Memento: The Video Memory Game', 'Description': 'Indicate which videos you remember by playing a simple memory game on short 3 second videos!', 'Question': '<ExternalQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2006-07-14/ExternalQuestion.xsd">\n<ExternalURL>https://memento-game.csail.mit.edu/</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>', 'Keywords': 'videos, memorability, memory, game, fun', 'HITStatus': 'Assignable', 'MaxAssignments': 1, 'Reward': '1.00', 'AutoApprovalDelayInSeconds': 604800, 'Expiration': datetime.datetime(2019, 3, 5, 10, 21, 25, tzinfo=tzlocal()), 'AssignmentDurationInSeconds': 1200, 'QualificationRequirements': [{'QualificationTypeId': '00000000000000000071'

{'HIT': {'HITId': '368IUKXGA7N6ZJOYYEM3ELA1ZNV6P2', 'HITTypeId': '3YWCO65Q5IJFBBBHQUQRP5I9B3WQ03', 'HITGroupId': '3CL9ACF21N3XOSJBS5A8GX3DPU6W65', 'CreationTime': datetime.datetime(2019, 3, 4, 4, 48, 6, tzinfo=tzlocal()), 'Title': 'Memento: The Video Memory Game', 'Description': 'Indicate which videos you remember by playing a simple memory game on short 3 second videos!', 'Question': '<ExternalQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2006-07-14/ExternalQuestion.xsd">\n<ExternalURL>https://memento-game.csail.mit.edu/</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>', 'Keywords': 'videos, memorability, memory, game, fun', 'HITStatus': 'Assignable', 'MaxAssignments': 1, 'Reward': '1.00', 'AutoApprovalDelayInSeconds': 604800, 'Expiration': datetime.datetime(2019, 3, 5, 10, 21, 26, tzinfo=tzlocal()), 'AssignmentDurationInSeconds': 1200, 'QualificationRequirements': [{'QualificationTypeId': '00000000000000000071', 'Comparator': 'Eq

{'HIT': {'HITId': '3UQVX1UPFUWFT11DURVA97SHBAH20A', 'HITTypeId': '3YWCO65Q5IJFBBBHQUQRP5I9B3WQ03', 'HITGroupId': '3CL9ACF21N3XOSJBS5A8GX3DPU6W65', 'CreationTime': datetime.datetime(2019, 3, 4, 4, 48, 6, tzinfo=tzlocal()), 'Title': 'Memento: The Video Memory Game', 'Description': 'Indicate which videos you remember by playing a simple memory game on short 3 second videos!', 'Question': '<ExternalQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2006-07-14/ExternalQuestion.xsd">\n<ExternalURL>https://memento-game.csail.mit.edu/</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>', 'Keywords': 'videos, memorability, memory, game, fun', 'HITStatus': 'Assignable', 'MaxAssignments': 1, 'Reward': '1.00', 'AutoApprovalDelayInSeconds': 604800, 'Expiration': datetime.datetime(2019, 3, 5, 10, 21, 26, tzinfo=tzlocal()), 'AssignmentDurationInSeconds': 1200, 'QualificationRequirements': [{'QualificationTypeId': '00000000000000000071', 'Comparator': 'Eq

{'HIT': {'HITId': '3QGHA0EA0LF2P42U6RH6HV4P6L9BWN', 'HITTypeId': '3YWCO65Q5IJFBBBHQUQRP5I9B3WQ03', 'HITGroupId': '3CL9ACF21N3XOSJBS5A8GX3DPU6W65', 'CreationTime': datetime.datetime(2019, 3, 4, 4, 48, 7, tzinfo=tzlocal()), 'Title': 'Memento: The Video Memory Game', 'Description': 'Indicate which videos you remember by playing a simple memory game on short 3 second videos!', 'Question': '<ExternalQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2006-07-14/ExternalQuestion.xsd">\n<ExternalURL>https://memento-game.csail.mit.edu/</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>', 'Keywords': 'videos, memorability, memory, game, fun', 'HITStatus': 'Assignable', 'MaxAssignments': 1, 'Reward': '1.00', 'AutoApprovalDelayInSeconds': 604800, 'Expiration': datetime.datetime(2019, 3, 5, 10, 21, 27, tzinfo=tzlocal()), 'AssignmentDurationInSeconds': 1200, 'QualificationRequirements': [{'QualificationTypeId': '00000000000000000071', 'Comparator': 'Eq

{'HIT': {'HITId': '3DTJ4WT8BFU4Q2JJR533H74SQKPZE0', 'HITTypeId': '3YWCO65Q5IJFBBBHQUQRP5I9B3WQ03', 'HITGroupId': '3CL9ACF21N3XOSJBS5A8GX3DPU6W65', 'CreationTime': datetime.datetime(2019, 3, 4, 4, 48, 8, tzinfo=tzlocal()), 'Title': 'Memento: The Video Memory Game', 'Description': 'Indicate which videos you remember by playing a simple memory game on short 3 second videos!', 'Question': '<ExternalQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2006-07-14/ExternalQuestion.xsd">\n<ExternalURL>https://memento-game.csail.mit.edu/</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>', 'Keywords': 'videos, memorability, memory, game, fun', 'HITStatus': 'Assignable', 'MaxAssignments': 1, 'Reward': '1.00', 'AutoApprovalDelayInSeconds': 604800, 'Expiration': datetime.datetime(2019, 3, 5, 10, 21, 28, tzinfo=tzlocal()), 'AssignmentDurationInSeconds': 1200, 'QualificationRequirements': [{'QualificationTypeId': '00000000000000000071', 'Comparator': 'Eq

...

{'HIT': {'HITId': '3UZUVSO3P9A4RVK0CGD9958JBG8EMZ', 'HITTypeId': '3YWCO65Q5IJFBBBHQUQRP5I9B3WQ03', 'HITGroupId': '3CL9ACF21N3XOSJBS5A8GX3DPU6W65', 'CreationTime': datetime.datetime(2019, 3, 4, 4, 48, 14, tzinfo=tzlocal()), 'Title': 'Memento: The Video Memory Game', 'Description': 'Indicate which videos you remember by playing a simple memory game on short 3 second videos!', 'Question': '<ExternalQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2006-07-14/ExternalQuestion.xsd">\n<ExternalURL>https://memento-game.csail.mit.edu/</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>', 'Keywords': 'videos, memorability, memory, game, fun', 'HITStatus': 'Assignable', 'MaxAssignments': 1, 'Reward': '1.00', 'AutoApprovalDelayInSeconds': 604800, 'Expiration': datetime.datetime(2019, 3, 5, 10, 21, 34, tzinfo=tzlocal()), 'AssignmentDurationInSeconds': 1200, 'QualificationRequirements': [{'QualificationTypeId': '00000000000000000071', 'Comparator': 'E

{'HIT': {'HITId': '3TX9T2ZCBBGY725AC5X93DBSXOUWZD', 'HITTypeId': '3YWCO65Q5IJFBBBHQUQRP5I9B3WQ03', 'HITGroupId': '3CL9ACF21N3XOSJBS5A8GX3DPU6W65', 'CreationTime': datetime.datetime(2019, 3, 4, 4, 48, 17, tzinfo=tzlocal()), 'Title': 'Memento: The Video Memory Game', 'Description': 'Indicate which videos you remember by playing a simple memory game on short 3 second videos!', 'Question': '<ExternalQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2006-07-14/ExternalQuestion.xsd">\n<ExternalURL>https://memento-game.csail.mit.edu/</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>', 'Keywords': 'videos, memorability, memory, game, fun', 'HITStatus': 'Assignable', 'MaxAssignments': 1, 'Reward': '1.00', 'AutoApprovalDelayInSeconds': 604800, 'Expiration': datetime.datetime(2019, 3, 5, 10, 21, 37, tzinfo=tzlocal()), 'AssignmentDurationInSeconds': 1200, 'QualificationRequirements': [{'QualificationTypeId': '00000000000000000071', 'Comparator': 'E

{'HIT': {'HITId': '3RKHNXPHGYBQQ3HJH4FYYA2I8Z6UKQ', 'HITTypeId': '3YWCO65Q5IJFBBBHQUQRP5I9B3WQ03', 'HITGroupId': '3CL9ACF21N3XOSJBS5A8GX3DPU6W65', 'CreationTime': datetime.datetime(2019, 3, 4, 4, 48, 18, tzinfo=tzlocal()), 'Title': 'Memento: The Video Memory Game', 'Description': 'Indicate which videos you remember by playing a simple memory game on short 3 second videos!', 'Question': '<ExternalQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2006-07-14/ExternalQuestion.xsd">\n<ExternalURL>https://memento-game.csail.mit.edu/</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>', 'Keywords': 'videos, memorability, memory, game, fun', 'HITStatus': 'Assignable', 'MaxAssignments': 1, 'Reward': '1.00', 'AutoApprovalDelayInSeconds': 604800, 'Expiration': datetime.datetime(2019, 3, 5, 10, 21, 38, tzinfo=tzlocal()), 'AssignmentDurationInSeconds': 1200, 'QualificationRequirements': [{'QualificationTypeId': '00000000000000000071', 'Comparator': 'E

{'HIT': {'HITId': '3MDWE879UJHRD8PMDG7E3BWE8KO9BV', 'HITTypeId': '3YWCO65Q5IJFBBBHQUQRP5I9B3WQ03', 'HITGroupId': '3CL9ACF21N3XOSJBS5A8GX3DPU6W65', 'CreationTime': datetime.datetime(2019, 3, 4, 4, 48, 18, tzinfo=tzlocal()), 'Title': 'Memento: The Video Memory Game', 'Description': 'Indicate which videos you remember by playing a simple memory game on short 3 second videos!', 'Question': '<ExternalQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2006-07-14/ExternalQuestion.xsd">\n<ExternalURL>https://memento-game.csail.mit.edu/</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>', 'Keywords': 'videos, memorability, memory, game, fun', 'HITStatus': 'Assignable', 'MaxAssignments': 1, 'Reward': '1.00', 'AutoApprovalDelayInSeconds': 604800, 'Expiration': datetime.datetime(2019, 3, 5, 10, 21, 38, tzinfo=tzlocal()), 'AssignmentDurationInSeconds': 1200, 'QualificationRequirements': [{'QualificationTypeId': '00000000000000000071', 'Comparator': 'E

{'HIT': {'HITId': '3566S7OX5FYMMRJ1WMG5J3SZRI971Y', 'HITTypeId': '3YWCO65Q5IJFBBBHQUQRP5I9B3WQ03', 'HITGroupId': '3CL9ACF21N3XOSJBS5A8GX3DPU6W65', 'CreationTime': datetime.datetime(2019, 3, 4, 4, 48, 19, tzinfo=tzlocal()), 'Title': 'Memento: The Video Memory Game', 'Description': 'Indicate which videos you remember by playing a simple memory game on short 3 second videos!', 'Question': '<ExternalQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2006-07-14/ExternalQuestion.xsd">\n<ExternalURL>https://memento-game.csail.mit.edu/</ExternalURL>\n  <FrameHeight>700</FrameHeight>\n</ExternalQuestion>', 'Keywords': 'videos, memorability, memory, game, fun', 'HITStatus': 'Assignable', 'MaxAssignments': 1, 'Reward': '1.00', 'AutoApprovalDelayInSeconds': 604800, 'Expiration': datetime.datetime(2019, 3, 5, 10, 21, 39, tzinfo=tzlocal()), 'AssignmentDurationInSeconds': 1200, 'QualificationRequirements': [{'QualificationTypeId': '00000000000000000071', 'Comparator': 'E

# HIT monitoring helpers

Helper functions that will be useful for monitoring the status of your HIT. See next section for how to use them.

In [8]:
# Contacts MTurk API to get all assignments for a HIT
# Returns them in a list. 
def get_all_assignments(hitid): 
    assignments = []
    should_continue = True
    next_token = False
    while (should_continue): 
        args = {
            'HITId': hitid, 
            'MaxResults': 100
        }
        if (next_token): 
            args['NextToken'] = next_token
        r = cl.list_assignments_for_hit(**args)
        next_token = r.get('NextToken', False)
        assignments.extend(r["Assignments"])
        should_continue = len(r["Assignments"]) > 0
    return assignments

# Summarizes all hits in `hits` in a human-readable way. 
# Prints out the HIT Title, id, if it is expired, and how many assignments it has
# completed, pending, and left for work. 
def summarize_hits(hits): 
    print(len(hits))
    ret = ""
    for hit in hits: 
        expiration = hit['Expiration'].replace(tzinfo=None)
        is_expired = expiration < datetime.datetime.now()
        description = ("Title: {title}\n" 
        "ID: {hid}\n"
        "\tAssignments left: {left}\n"
        "\tAssignments completed: {complete}\n"
        "\tAssignments pending: {pending}\n"
        "\tExpired: {exp}\n\n").format(
            title=hit['Title'], 
            hid=hit['HITId'], 
            left=hit['NumberOfAssignmentsAvailable'], 
            complete=hit['NumberOfAssignmentsCompleted'], 
            pending=hit['NumberOfAssignmentsPending'],
            exp=str(is_expired)
        )
        ret += description
    print(ret)
    
# Prints a human-readable summary of all pending/submitted/approved assignments for all hits in `hits`
def summarize_assignments(hits):
    ret = ""
    for hit in hits: 
        hid = hit['HITId']
        title =  hit['Title']
        name = "HIT %s: %s" % (hid, title)
        ret += name + "\n"
        assignments = get_all_assignments(hid)
        if len(assignments) == 0: 
            ret += "\tNo pending/submitted/approved assignments for this HIT\n"
        for a in assignments: 
            desc = "\tAssignment {aid}\n\t\tStatus: {status}\n".format(aid=a['AssignmentId'], status=a['AssignmentStatus'])
            ret += desc
    print(ret)
    
# Refreshes data about the requested hits
def refresh_hits(): 
    global hits 
    global MAX_RESULTS
    hits = cl.list_hits(MaxResults=MAX_RESULTS)['HITs']

# HIT monitoring

In [9]:
MAX_RESULTS = 100 # set equal to the number of outstanding hits you have 

# API call to grab HIT data from MTurk 
hits = cl.list_hits(MaxResults=MAX_RESULTS)['HITs']

In [10]:
# Summarizes all outstanding HITs
refresh_hits()
summarize_hits(hits)

100
Title: Memento: The Video Memory Game
ID: 3566S7OX5FYMMRJ1WMG5J3SZRI971Y
	Assignments left: 0
	Assignments completed: 0
	Assignments pending: 0
	Expired: False

Title: Memento: The Video Memory Game
ID: 3FDWKV9VCPHLGRHM2GSEDNUMX41UMV
	Assignments left: 0
	Assignments completed: 0
	Assignments pending: 0
	Expired: False

Title: Memento: The Video Memory Game
ID: 3T2HW4QDUXMANDHSRG39EV2WQ5O9C2
	Assignments left: 0
	Assignments completed: 0
	Assignments pending: 0
	Expired: False

Title: Memento: The Video Memory Game
ID: 3QE4DGPGBTQM7JRLC731NECV2524GB
	Assignments left: 0
	Assignments completed: 0
	Assignments pending: 0
	Expired: False

Title: Memento: The Video Memory Game
ID: 3UOMW19E6FLRMQFGOQQS2FXU495C5E
	Assignments left: 0
	Assignments completed: 0
	Assignments pending: 0
	Expired: False

Title: Memento: The Video Memory Game
ID: 3GONHBMNHXD22QBW83RMUF91ZMGZMP
	Assignments left: 0
	Assignments completed: 0
	Assignments pending: 0
	Expired: False

Title: Memento: The Video Memo

In [11]:
# Summarizes assignments for all oustanding HITs 
refresh_hits()
summarize_assignments(hits)


HIT 3566S7OX5FYMMRJ1WMG5J3SZRI971Y: Memento: The Video Memory Game
	Assignment 3ON104KXQNBKRPFFHECKX1T77J2W4I
		Status: Submitted
HIT 3FDWKV9VCPHLGRHM2GSEDNUMX41UMV: Memento: The Video Memory Game
	Assignment 3UWN2HHPU1KD6G8CFEHFZLWMSN0SNT
		Status: Submitted
HIT 3T2HW4QDUXMANDHSRG39EV2WQ5O9C2: Memento: The Video Memory Game
	Assignment 3VAR3R6G1SGD5HTF2VBNXJWQ63YO84
		Status: Submitted
HIT 3QE4DGPGBTQM7JRLC731NECV2524GB: Memento: The Video Memory Game
	Assignment 3NVC2EB65TE3YYRBW1PP8TMH4R5Y3X
		Status: Submitted
HIT 3UOMW19E6FLRMQFGOQQS2FXU495C5E: Memento: The Video Memory Game
	Assignment 3FE7TXL1LL254E461RUQCXENZ4P2QO
		Status: Submitted
HIT 3GONHBMNHXD22QBW83RMUF91ZMGZMP: Memento: The Video Memory Game
	Assignment 337RC3OW08H3A8MVXW65XGC4MWUVLZ
		Status: Submitted
HIT 3UV0D2KX1OYGTJVQ1NXJ5TCJ1Q24FC: Memento: The Video Memory Game
	Assignment 3GNA64GUZHJX3BNTJAWOA4HZJEI5QU
		Status: Submitted
HIT 3W3RSPVVGU61A9Z124RZDAFXXZBULT: Memento: The Video Memory Game
	Assignment 3II4UPYCOMM

# Approve HITs

Approves all outstanding assignments for the HITs displayed above. 

In [13]:
def approve_all(hits): 
    num_approved = 0
    for hit in hits: 
        # make sure you keep getting assignments 
        assignments = get_all_assignments(hit["HITId"])
#         print(assignments)
        for a in assignments: 
            if a['AssignmentStatus'] != 'Approved':
                print("Approving assignment")
                num_approved += 1
                cl.approve_assignment(AssignmentId=a['AssignmentId'])
    print("Approved %d assignments" % num_approved)

# def approve_all(assignments): 
#     for a in assignments: 
        
#         print(a)
#         cl.approve_assignment(AssignmentId=a['AssignmentId'])
#     print("Succesfully approved %d assignments" % len(assignments))

In [14]:
# refresh_hits()
approve_all(hits)

Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving assignment
Approving ass

# Update expiration or num tasks

In [ ]:
# changes the expiration date on a HIT to days_from_now days in the future
def update_expiration(hitid, days_from_now): 
    if ALLOW_UPDATE_EXPIRATION: 
        days = days_from_now*datetime.timedelta(days=1)
        expire_time = datetime.datetime.now() + days

        response = cl.update_expiration_for_hit(HITId=hitid, ExpireAt=expire_time)
        print(response)
        return response
    else: 
        raise RuntimeError("This action is not currently enabled; set `ALLOW_UPDATE_EXPIRATION` to true to proceed with this action")
    
def expire_hit(hit): 
    return update_expiration(hit, -10)

In [ ]:
def add_assignments(hitid, num_assignments): 
    if ALLOW_ASSIGNMENT_ADDITION: 
        response = cl.create_additional_assignments_for_hit(
            HITId=hitid,
            NumberOfAdditionalAssignments=num_assignments
        )
        print(response)
        return response
    else: 
        raise RuntimeError("This action is not currently enabled; set `ALLOW_ASSIGNMENT_ADDITION` to true to proceed with this action")

In [ ]:
# Use this cell to expire a HIT 
HIT_id_to_expire = "FILL THIS IN" 
expire_hit(HIT_id_to_expire)

In [ ]:
# Use this cell to add assignments to a HIT 
HIT_id_to_add_assignments = "FILL THIS IN"
num_assignments_to_add = 0
add_assignments(HIT_id_to_add_assignments, num_assignments_to_add)

# Add custom qualifications 

## Add a qualification to disqualify workers who have done work before

- uses "negative qualification" method from https://github.com/cloudyr/MturkR/wiki/qualifications-as-blocks

#### NOTE: quals are kept separate for the sandbox and prod. Make sure you are creating and assigning your quals in prod. 

### Structure of a new qualification

In [18]:
NEW_QUAL = {
    'Name': 'qualName',
    'Keywords': 'Keywords for qual',
    'Description': 'What is this qual, and why are you assigning it?',
    'QualificationTypeStatus': 'Active',
    'AutoGranted': False
}

### Helpers for creating, viewing, and assigning qualifications

In [19]:
# Registers a custom qualification with MTurk 
def create_qual(new_qual):
    if ALLOW_CREATE_QUAL: 
        response = cl.create_qualification_type(**new_qual)
        print(response)
        Id = response['QualificationTypeId']
        print("id", Id)
        return Id
    else: 
        raise RuntimException("This action is not currently enabled; set `ALLOW_CREATE_QUAL` to true to proceed with this action")
        
# Gets all the custom quals you have created and prints them
def list_quals(): 
    response = cl.list_qualification_types(
            Query='hasCompletedVisualGraphRecallTask',
            MustBeRequestable=False
    )
    print(response)
    
# Assigns a qualification to a worker 
def assign_qual(qual_id, worker_ids): 
    for worker in worker_ids: 
        response = cl.associate_qualification_with_worker(
                QualificationTypeId=qual_id, 
                WorkerId=worker,
                IntegerValue=1,
                SendNotification=False
        )
        print(response)
        assert response
        
# Gets the ids of all workers who worked on a particular hit 
def get_workers_for_hit(hitid): 
    a = get_all_assignments(hitid)
    workers = [a_['WorkerId'] for a_ in a]
    return workers
    
# Confirms that every worker in worker_ids has qual with qual_id
def confirm_quals(qual_id, worker_ids): 
    for w in worker_ids: 
        response = cl.get_qualification_score(
                QualificationTypeId=qual_id,
                WorkerId=w
        )
        response = response['Qualification']
        assert response['Status'] == 'Granted'
        assert response['IntegerValue'] == 1
        
# Assigns qual with `qual_id` to every worker who has completed an assignment for the hit with `hitid`
def assign_qual_for_hit(hitid, qual_id): 
    workers = get_workers_for_hit(hitid)
    print("got workers")
    assign_qual(qual_id, workers)
    print("assigned qual")
    confirm_quals(qual_id, workers)
    print("confirmed qual")

### Use the following cells to manipulate qualifications

In [ ]:
# Use this cell to view the custom qualifications you have created
list_quals()

In [ ]:
# Use this cell to create a new qual 
qual_to_create = {}
create_qual(qual_to_create)

In [ ]:
# Use this cell to assign a custom qual to every worker who has done a specific HIT
hit_id = "FILL THIS IN"
qual_id_to_assign = "FILL THIS IN"
assign_qual_for_hit(hit_id, qual_id_to_assign)

# Create Compensation HIT

Mistakes happen, and sometimes they can lead to a worker who put in an honest effort being unable to complete a task and get paid. It's a good idea to compensate these workers when they reach out because it helps maintain relations with workers and is the right thing to do.

However, workers can only be paid upon completing a task. The workaround is to create a custom qualification, assign it to the worker you want to compensate, and create a no-work HIT requiring the custom qualification. This code does that.

In [20]:
# worker_ids is str[]
# compensation is str but should match the regex ^\d*\.\d\d$ (e.g. "1.00")
# for_hit_id is str -- optional, but helpful for records
def compensate_workers(worker_ids, compensation, for_hit_id=""):
    with open('compensation.xml', 'r') as myfile:
        question_xml=myfile.read()

    keywords = 'compensation'
    description = 'Compensation for HIT'
    if for_hit_id:
        keywords += ', ' + for_hit_id
        description += ' ' + for_hit_id

    # create qual, assign to workers
    custom_qual = {
        'Name': str(uuid4()), # a qual must have a unique name
        'Keywords': keywords,
        'Description': description,
        'QualificationTypeStatus': 'Active',
        'AutoGranted': False
    }
    qual_id = create_qual(custom_qual)
    assign_qual(qual_id, worker_ids)

    # create HIT requiring qual
    task = {
        'numAssignments': len(worker_ids),
        'lifetime': 3 * 24 * 60 * 60, # 3 days
        'duration': 5 * 60, # 5 min
        'rewardAmount': compensation,
        'title': description,
        'keywords': keywords,
        'description': description,
    }
    quals = [{
        'QualificationTypeId': qual_id,
        'Comparator': 'Exists',
        'ActionsGuarded': 'DiscoverPreviewAndAccept'
    }]
    create_hit(task, question_xml, quals)

In [21]:
worker_ids = [''] # worker_id strings in a list
compensation = "0.50" # change to the amount of dollars you want to give
for_hit_id = "" # hit_id string (what you are compensating for)
compensate_workers(worker_ids, compensation, for_hit_id)

NameError: name 'ALLOW_CREATE_QUAL' is not defined

# Download data

Helper to download data from MTurk 

In [22]:
from bs4 import BeautifulSoup as bs 
import pprint

def pretty_print(obj):
    pp = pprint.PrettyPrinter(indent=4)
    pp.pprint(obj)
    pp = None
    
def get_data_from_assignment(a): 
    a_xml = a['Answer']
    soup = bs(a_xml, "html.parser")
    answers = soup.find_all("answer")
    results = {'HITId': a['HITId'], 'AssignmentId': a['AssignmentId'], 'WorkerId': a['WorkerId']}
    for ans in answers: 
        identifier = ans.find('questionidentifier').string
        answer = ans.find('freetext').string
        try: 
            results[identifier] = json.loads(answer)
        except:
            results[identifier] = answer
    return results

# Downloads all the assignments completed for `hits` as a list of dictionaries. 
# If a download_path is given, also saves that data as json 
def get_assignment_content(hits, download_path="", should_print=False): 
    all_responses = []
    for hit in hits: 
        hitid = hit['HITId']
        assignments = get_all_assignments(hitid)
        for a in assignments:
            results = get_data_from_assignment(a)
            all_responses.append(results)
    if should_print: 
        pretty_print(all_responses)
    if download_path: 
        with open(download_path, 'w') as outfile: 
            json.dump(all_responses, outfile)
    return all_responses

_string_clean = lambda s: s.strip().lower()

def test_assignments_for_approval(hits, condition=lambda x: True): 
    to_approve = []
    to_reject = [] 
    for hit in hits: 
        # make sure you keep getting assignments 
        assignments = get_all_assignments(hit["HITId"])
        #print(assignments)
        for a_raw in assignments: 
            a = get_data_from_assignment(a_raw)
            if a_raw['AssignmentStatus'] != 'Approved':
                print("Testing assignment")
                data = condition(a)
                if (data): 
                    print("\tApproved")
                    to_approve.append(a)
                else: 
                    print("\tRejected")
                    to_reject.append(a)
    print("Found %d assignments to approve" % len(to_approve))
    print("Found %d assignments to reject" % len(to_reject))
    return to_approve, to_reject

def approve_all(assignments): 
    for a in assignments: 
        cl.approve_assignment(AssignmentId=a['AssignmentId'])
    print("Succesfully approved %d assignments" % len(assignments))

def get_levels_table(): 
    # WARNING: this assumes you have dumped the most recent version of the db into the folder dump/
    rows = []
    with open(os.path.join("..", "dump", "levels.tsv")) as tsvfile:
        reader = csv.reader(tsvfile, delimiter='\t')
        is_header = True
        headers = {}
        for row in reader:
            if is_header: 
                for i, elt in enumerate(row): 
                    headers[i] = elt
                is_header = False
            else: 
                data = dict([(val, row[key]) for key, val in headers.items()])
                rows.append(data)
    return rows

def is_valid_assignment(a, levels): 
    possible_levels = [l for l in levels if l['assignment_id'] == a['AssignmentId'] and l['score'] is not 'NULL']
    if not possible_levels: 
        return False
    return True

    
    #try: 
    return True
#     except Exception as e: 
#         print("error", e)
#         return False


In [23]:
# Use this cell to download data
responses = get_assignment_content(hits, download_path='../dump/100responses.json', should_print=True)
pass

[   {   'AssignmentId': '3ON104KXQNBKRPFFHECKX1T77J2W4I',
        'HITId': '3566S7OX5FYMMRJ1WMG5J3SZRI971Y',
        'WorkerId': 'A3RKY9YC2DYCW9',
        'feedback': 'fun',
        'results': {   'inputs': {   'level': 1,
                                     'levelID': 453,
                                     'videos': [   {   'type': 'target',
                                                       'url': 'landing/flickr-6-0-4-7-4-9-5-3-10360474953_2.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'eating/flickr-4-3-0-2-2-9-2-4-6243022924_4.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'walking/flickr-5-3-5-4-7-1-0-0-2653547100_8.mp4'},
                                                   {   'type': 'vig',
                                                       'url': 'sitting/flickr-9-8-4-6-6-8-5-3

                                        {   'durationMsec': 836,
                                            'response': True,
                                            'startMsec': 221628},
                                        {   'durationMsec': 3461,
                                            'response': False,
                                            'startMsec': 222681},
                                        {   'durationMsec': 795,
                                            'response': True,
                                            'startMsec': 226145},
                                        {   'durationMsec': 4501,
                                            'response': False,
                                            'startMsec': 227154},
                                        {   'durationMsec': 3895,
                                            'response': False,
                                            'startMsec': 231660},
                             

                                                   {   'type': 'vig_repeat',
                                                       'url': 'skiing/flickr-4-1-0-1-9-7-3-3-4441019733_18.mp4'},
                                                   {   'type': 'target_repeat',
                                                       'url': 'running/flickr-0-7-7-8-6-5-6-3-5107786563_1.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'marching/flickr-8-2-8-2-7-8-8-8-4582827888_2.mp4'},
                                                   {   'type': 'vig',
                                                       'url': 'carrying/flickr-3-9-0-1-2-9-0-4-5139012904_4.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'writing/flickr-1-7-6-8-9-2-5-6-3117689256_10.mp4'},
                                                   {  

                                        {   'durationMsec': 3169,
                                            'response': False,
                                            'startMsec': 131337},
                                        {   'durationMsec': 3131,
                                            'response': False,
                                            'startMsec': 134514},
                                        {   'durationMsec': 3132,
                                            'response': False,
                                            'startMsec': 137648},
                                        {   'durationMsec': 324,
                                            'response': True,
                                            'startMsec': 140786},
                                        {   'durationMsec': 533,
                                            'response': True,
                                            'startMsec': 143888},
                             

                                                       'url': 'walking/flickr-7-0-7-9-8-5-0-5-3670798505_4.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'planting/flickr-7-2-2-7-6-6-1-0-23372276610_22.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'standing/4-2-5-3947121425.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'brushing/flickr-5-5-9-2-0-6-8-7-6255920687_9.mp4'},
                                                   {   'type': 'vig',
                                                       'url': 'joining/flickr-3-0-3-4844566303_17.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'flying/7-5-4-9-6-3-3-9-30754

...

                                        {   'durationMsec': 3377,
                                            'response': False,
                                            'startMsec': 143940},
                                        {   'durationMsec': 3259,
                                            'response': False,
                                            'startMsec': 147325},
                                        {   'durationMsec': 305,
                                            'response': True,
                                            'startMsec': 163493},
                                        {   'durationMsec': 285,
                                            'response': True,
                                            'startMsec': 163977},
                                        {   'durationMsec': 800,
                                            'response': False,
                                            'startMsec': 170687},
                              

                                                       'url': 'dancing/flickr-4-8-3-6-9-4-1-1-9048369411_130.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'shooting/flickr-4-7-6-4-6-5-8-6-2847646586_1.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'performing/flickr-7-2-2-5060936722_66.mp4'},
                                                   {   'type': 'vig',
                                                       'url': 'competing/7-4-3-6-5-6-5-3-7974365653.mp4'},
                                                   {   'type': 'vig_repeat',
                                                       'url': 'drinking/flickr-6-3-0-4-3-8-9-5-3363043895_1.mp4'},
                                                   {   'type': 'target',
                                                       'url': 'eating/fli

                                            'startMsec': 190010},
                                        {   'durationMsec': 3138,
                                            'response': False,
                                            'startMsec': 193150},
                                        {   'durationMsec': 3138,
                                            'response': False,
                                            'startMsec': 196290},
                                        {   'durationMsec': 3139,
                                            'response': False,
                                            'startMsec': 199430},
                                        {   'durationMsec': 953,
                                            'response': True,
                                            'startMsec': 202571},
                                        {   'durationMsec': 932,
                                            'response': True,
                             

                                                   {   'type': 'filler',
                                                       'url': 'boarding/flickr-4-5-6-0-1-2-7-0-5245601270_18.mp4'},
                                                   {   'type': 'target_repeat',
                                                       'url': 'climbing/flickr-4-8-5-0-9-3-1-3-3248509313_63.mp4'},
                                                   {   'type': 'filler',
                                                       'url': 'flowing/9-5-7-4519961957.mp4'},
                                                   {   'type': 'vig_repeat',
                                                       'url': 'dancing/flickr-4-4-7-4-5-1-0-6-2844745106_55.mp4'},
                                                   {   'type': 'vig',
                                                       'url': 'competing/6-1-6-7-0-3-6-5-8461670365.mp4'},
                                                   {   'type': 'target_repeat'

                                            'startMsec': 282828},
                                        {   'durationMsec': 1572,
                                            'response': False,
                                            'startMsec': 285493},
                                        {   'durationMsec': 3029,
                                            'response': False,
                                            'startMsec': 287068},
                                        {   'durationMsec': 3079,
                                            'response': False,
                                            'startMsec': 290100},
                                        {   'durationMsec': 3179,
                                            'response': False,
                                            'startMsec': 293183},
                                        {   'durationMsec': 3146,
                                            'response': False,
                         

In [ ]:
levels = get_levels_table()
condition = lambda a: is_valid_assignment(a, levels)
to_approve, to_reject = test_assignments_for_approval(hits, condition=condition)

In [ ]:
approve_all(to_approve)